In [1]:
# Check Environment

import sys
print(sys.version)
print(sys.executable)

3.7.5 (default, Oct 31 2019, 15:18:51) [MSC v.1916 64 bit (AMD64)]
C:\Users\Dennis\anaconda3\envs\rc_env_np16p6\python.exe


In [2]:
# IMPORTS

import rescomp
import numpy as np

import pandas as pd

import plotly.express as px

import matplotlib.pyplot as plt
# from mpl_toolkits import mplot3d

### Create Lorenz Dataset:

In [3]:
simulation_time_steps = 8000
dt = 2e-2

starting_point = np.array([-14.03020521, -20.88693127, 25.53545])
sim_data = rescomp.simulate_trajectory(
    sys_flag='lorenz', dt=dt, time_steps=simulation_time_steps,
    starting_point=starting_point)

### Create artificially "wrong" model and plot real and "fake" Lorenz Attractor:

In [4]:
#Create artificially "wrong" model by changing the system parameters:
eps1 = 0.0
eps2 = 0.0
eps3 = 0.0
model = lambda x: rescomp.simulations._normal_lorenz(x, sigma=10*(1+eps1), rho=28*(1+eps2), beta=8/3*(1+eps3))
# model = lambda x: -x

# model_pred = lambda x: x + model(x)*dt
model_pred = lambda x: rescomp.simulations._runge_kutta(model, dt, x)

# test it:
x = np.zeros((simulation_time_steps, 3))

x[0] = starting_point
for i in range(1, simulation_time_steps):
    x_i = x[i-1]
    x[i] = model_pred(x_i)


# Plotly
sim_data_df = pd.DataFrame(data=sim_data, columns = ["x", "y", "z"])
sim_data_df["name"] = "true"
wrong_model_data_df = pd.DataFrame(data=x, columns = ["x", "y", "z"])
wrong_model_data_df["name"] = "wrong"
df = pd.concat([sim_data_df, wrong_model_data_df])
fig = px.line_3d(df, x = "x", y ="y", z="z", color = "name")
fig.show()


# Matplotlib: 
# fig = plt.figure(figsize=(6, 3), dpi=300)
# ax = fig.add_subplot(111, projection='3d')
# ax.plot(x[:, 0], x[:, 1], x[:, 2],
#         alpha=0.8, color='blue', linewidth = 0.1)
# ax.plot(sim_data[:, 0], sim_data[:, 1], sim_data[:, 2],
#         alpha=0.8, color='red', linewidth = 0.1)
# ax.set_title("Normal Lorenz63 System Simulated")
# ax.set_xlabel('x')
# ax.set_ylabel('y')
# ax.set_zlabel('z')
# plt.show()

### Create "normal" and different Hybrid Models:

In [5]:
n_dim = 1000

ESNs = {}
settings_dict = {}

# The Baseline
np.random.seed(1)
name = "normal"
esn_normal = rescomp.esn.ESNWrapper()
esn_normal.create_network(n_dim = n_dim)
ESNs[name] = esn_normal

# Hybrid only at output: 
np.random.seed(1)
name = "hybrid out"
esn_hybrid_out = rescomp.esn.ESNHybrid()
esn_hybrid_out.create_network(n_dim = n_dim)
add_model_to_output = True
add_model_to_input = False
esn_hybrid_out.set_model(model_pred, add_model_to_input = add_model_to_input, add_model_to_output = add_model_to_output)
ESNs[name] = esn_hybrid_out

# Hybrid only at input:
np.random.seed(1)
name = "hybrid in"
esn_hybrid_in = rescomp.esn.ESNHybrid()
esn_hybrid_in.create_network(n_dim = n_dim)
add_model_to_output = False
add_model_to_input = True
gamma = 0.5
esn_hybrid_in.set_model(model_pred, add_model_to_input = add_model_to_input,
                        add_model_to_output = add_model_to_output,
                       gamma = gamma)
ESNs[name] = esn_hybrid_in

# Hybrid at in- and output: 
np.random.seed(1)
name = "hybrid both"
esn_hybrid_both = rescomp.esn.ESNHybrid()
esn_hybrid_both.create_network(n_dim = n_dim)
add_model_to_output = True
add_model_to_input = True
gamma = 0.5
esn_hybrid_both.set_model(model_pred, add_model_to_input = add_model_to_input,
                        add_model_to_output = add_model_to_output,
                       gamma = gamma)
ESNs[name] = esn_hybrid_both

# The Test
np.random.seed(1)
name = "test"
esn_normal = rescomp.esn.ESNWrapper()
esn_normal.create_network(n_dim = n_dim, )
ESNs[name] = esn_normal

### Train and predict:

In [20]:
train_sync_steps = 500
train_steps = 6000
pred_steps = 1500 

# For testing different W_in settings
w_in_sparse=True #True
w_in_ordered=True #False
w_in_no_update=False #False
act_fct_flag='tanh_simple' #'tanh_simple'
w_out_fit_flag="simple" #"simple"
reg_param = 1e-10

ESNs_results = {}

for name, ESN in ESNs.items():
    print("---- Training and predicting " + name + " ----")
    if name == "test": # temporary individual settings for each one -> programm it better
        w_out_fit_flag="linear_and_square_r_alt"
    
    ESN.train(x_train=sim_data[:train_sync_steps + train_steps], sync_steps=train_sync_steps, reg_param=reg_param, 
             w_in_sparse=w_in_sparse, 
             w_in_ordered=w_in_ordered, w_in_no_update=w_in_no_update, act_fct_flag=act_fct_flag, 
             w_out_fit_flag=w_out_fit_flag)
    
    out = ESN.predict(sim_data[train_sync_steps + train_steps-1:])
    print(out[0].shape)
    ESNs_results[name] = out
#     ESNs_results[name] = ESN.train_and_predict(
#         x_data=sim_data, train_sync_steps=train_sync_steps, train_steps=train_steps, 
#         pred_steps=pred_steps, 
#         w_in_sparse=w_in_sparse, w_in_ordered=w_in_ordered, w_in_no_update=w_in_no_update, act_fct_flag=act_fct_flag, 
#         w_out_fit_flag=w_out_fit_flag, reg_param = reg_param
#         )

---- Training and predicting normal ----
(1500, 3)
---- Training and predicting hybrid out ----
(1500, 3)
---- Training and predicting hybrid in ----
(1500, 3)
---- Training and predicting hybrid both ----
(1500, 3)
---- Training and predicting test ----
(1500, 3)


In [24]:
# testing:
print(sim_data.shape)
x_train, x_pred = rescomp.utilities.train_and_predict_input_setup(sim_data, train_sync_steps = train_sync_steps, 
                                                train_steps = train_steps, 
                                                pred_steps = pred_steps)

print(x_train.shape, x_pred.shape)

print(x_train[train_sync_steps + train_steps-1] == x_pred[0])

(8000, 3)
(6500, 3) (1501, 3)
[ True  True  True]


### Create Dataframe used for plotting (plotly):

In [7]:
frames = []

get_test = True
for name, result in ESNs_results.items():
    y_pred, y_test = result
    
    if get_test:
        df_test = pd.DataFrame(data=y_test, columns = ["x", "y", "z"])
        df_test["name"] = "test"
        frames.append(df_test)
        get_test = False
    df_pred = pd.DataFrame(data=y_pred, columns = ["x", "y", "z"])
    df_pred["name"] = name + " pred"
    frames.append(df_pred)
        
df = pd.concat(frames)
print(df)

             x         y          z       name
0     1.955340  3.594315   9.957817       test
1     2.315795  4.292259   9.604431       test
2     2.750612  5.135080   9.337862       test
3     3.275032  6.149423   9.183554       test
4     3.906541  7.363522   9.178585       test
...        ...       ...        ...        ...
1495 -2.775629 -5.095149  22.590536  test pred
1496 -3.217783 -5.342762  21.722062  test pred
1497 -3.633959 -5.690126  20.961930  test pred
1498 -4.047105 -6.138568  20.315558  test pred
1499 -4.476199 -6.688720  19.792744  test pred

[9000 rows x 4 columns]


### Plot x coordinate of models: prediction vs test:

In [8]:
fig = px.line(df, y="x", color='name')
fig.show()

### Plot attractor: 

In [9]:
fig = px.line_3d(df,x = "x", y ="y", z="z", color='name')
fig.show()

### Create Dataframe for RMSE:

In [10]:
frames = []

for name, result in ESNs_results.items():
    y_pred, y_test = result
    rmse = rescomp.measures.rmse_over_time(y_pred, y_test)
    df_rmse = pd.DataFrame(data=rmse, columns = ["rmse"])
    df_rmse["name"] = "rmse " + name
    frames.append(df_rmse)
        
df_rmse = pd.concat(frames)
print(df_rmse)

          rmse         name
0     0.000142  rmse normal
1     0.000183  rmse normal
2     0.000224  rmse normal
3     0.000308  rmse normal
4     0.000414  rmse normal
...        ...          ...
1495  6.669654    rmse test
1496  6.773045    rmse test
1497  6.956191    rmse test
1498  7.214834    rmse test
1499  7.549254    rmse test

[7500 rows x 2 columns]


### Plot RMSE:

In [11]:
fig = px.line(df_rmse, y="rmse", color='name')
fig.show()

### Plot the average output weights (if model is added to output):

In [12]:
def get_info_about_output_weights(esn):
    n_dim = esn._n_dim
    rc_weights = esn._w_out[:, : n_dim]
    model_weights = esn._w_out[:, n_dim:]
    

    
    avg_abs_rc_weight = np.average(np.abs(rc_weights))
    avg_abs_model_weight = np.average(np.abs(model_weights))
    return avg_abs_rc_weight, avg_abs_model_weight

for esn_name in ["hybrid out", "hybrid both"]:
    print("______________")
    print(f"{esn_name}: ")
    esn = ESNs[esn_name]
    avg_abs_rc_weight, avg_abs_model_weight = get_info_about_output_weights(esn)
    print(f"avg_abs_rc_weight: {avg_abs_rc_weight}")
    print(f"avg_abs_model_weight: {avg_abs_model_weight}")

# modify _w_out:
def get_modified_w_out(n_dim, state_dim):
    matrix = np.zeros((state_dim, n_dim))
    print(matrix)
    print(matrix[:, 0])
    for i in range(0,state_dim):
        to_add = np.zeros(state_dim)
        to_add[i] = 1
        matrix[:, n_dim - state_dim +i] = to_add
    return matrix

n_dim = 5
state_dim = 3
get_modified_w_out(n_dim, state_dim)

______________
hybrid out: 
avg_abs_rc_weight: 0.1521261140917845
avg_abs_model_weight: 0.3332522338498778
______________
hybrid both: 
avg_abs_rc_weight: 0.17190336928533206
avg_abs_model_weight: 0.3339550141471204
[[0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0.]]
[0. 0. 0.]


array([[0., 0., 1., 0., 0.],
       [0., 0., 0., 1., 0.],
       [0., 0., 0., 0., 1.]])

-----------------------------------
# OLD

In [13]:
# print(esn_hybrid._w_out.shape)
# print(esn_normal._w_out.shape)

# print(np.average(esn_hybrid._w_out[:, -3:]))
# print(np.average(esn_hybrid._w_out[:, :-3]))

In [14]:
# fig1 = plt.figure(figsize=(9, 6), dpi=300)
# ax1 = fig1.add_subplot(111, projection='3d')

# ax1.plot(y_test_normal[:, 0], y_test_normal[:, 1], y_test_normal[:, 2],
#         alpha=0.8, color='blue', label='simulation')
# ax1.plot(y_pred_normal[:, 0], y_pred_normal[:, 1], y_pred_normal[:, 2],
#         alpha=0.8, color='orange', label='pred normal')
# ax1.plot(y_pred_hybrid[:, 0], y_pred_hybrid[:, 1], y_pred_hybrid[:, 2],
#         alpha=0.8, color='red', label='pred hybrid')

# start = y_test_normal[0]
# ax1.plot([start[0]], [start[1]], [start[2]], 
#          color='black', linestyle='', marker='o', label='starting point')

# ax1.set_title("Simulation vs Prediction")
# ax1.set_xlabel('x')
# ax1.set_ylabel('y')
# ax1.set_zlabel('z')
# plt.legend()
# plt.show()

In [15]:
# prediction_dict = {}

# y_test = None

# fig2 = plt.figure(figsize=(9, 6), dpi=300)
# ax2 = fig2.add_subplot(1, 1, 1)

# for name, prediction in prediction_dict.items():
#     rmse = rescomp.measures.rmse_over_time(time_series, y_test)
#     ax2.plot(rmse, linestyle='--', label=name)
#     print("AVG RMSE for " + name, np.average(rmse))

# ax2.set_title("RMSE")
# ax2.set_xlabel('time steps')
# ax2.set_ylabel('RMSE')
# plt.legend()
# plt.show()

In [16]:
n_dim = 100
avg_deg = 3
p = 0.4 # largest eigenvalue (spectral radius)

esn1 = rescomp.esn.ESNWrapper()
esn1.create_network(n_dim = n_dim, n_rad=p, n_avg_deg=avg_deg, n_type_flag="erdos_renyi_directed")

esn2 = rescomp.esn.ESNWrapper()
esn2.create_network(n_dim = n_dim, n_rad=p, n_avg_deg=avg_deg, n_type_flag="erdos_renyi")


In [17]:
print(np.argwhere(esn1._network).shape)
print("-----------------------------------------")
print(np.argwhere(esn2._network).shape)

(315, 2)
-----------------------------------------
(304, 2)


In [18]:
eps_list = np.linspace(0.004, 0.1, 25)
print(eps_list)

[0.004 0.008 0.012 0.016 0.02  0.024 0.028 0.032 0.036 0.04  0.044 0.048
 0.052 0.056 0.06  0.064 0.068 0.072 0.076 0.08  0.084 0.088 0.092 0.096
 0.1  ]


In [19]:
r = np.ones((5, 5))*2
r = np.ones((5))*2

r_gen = np.copy(r)
r_gen.T[::2] = r.T[::2] ** 2

print(r, r_gen)

[2. 2. 2. 2. 2.] [4. 2. 4. 2. 4.]
